# TABLE OF CONTENT : 
 1. [Scrapping Wikipedia Web page](#1)<br>
 2. [Adding coordinates of neighborhoods](#2)<br>
 3. [Folium maps](#3)<br>
 4. [Cluster neighborhoods](#4)<br>

In [1]:
#Installing beautifulsoup package
#!pip install beautifulsoup4

In [32]:
#import of libraries necessary to scrap the web page 
import pandas as pd
from bs4 import BeautifulSoup
import requests
import numpy as np
import folium
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

# 1. SCRAPPING WIKIPEDIA WEB PAGE <a id="1"></a>

In [2]:
url='https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M'
url

'https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M'

In [3]:
#parsing the web page wikipedia
page_response=requests.get(url,timeout=5)
page_content = BeautifulSoup(page_response.content, 'lxml')

In [4]:
#creation of the data frame containing the table from wikipedia page : 
# varibale with all the tables found in the page 
tables=page_content.find_all('table')
#focus on the table we are interested in : 
table=tables[0].tbody
#creation of our data frame :
df_table=pd.DataFrame(columns=['PostalCode','Borough','Neighborhood'])
#iteration in the table in order to extract content and add it to our dataframe 
for row in table.find_all('tr') : 
    cols=row.find_all('td')
    try : 
        df_table=df_table.append({'PostalCode':cols[0].text,
                                          'Borough': cols[1].text, 
                                          'Neighborhood': cols[2].text, 
                                         }, ignore_index=True)
    except: 
        pass

df_table

PostalCode             Borough  \
0        M1A\n      Not assigned\n   
1        M2A\n      Not assigned\n   
2        M3A\n        North York\n   
3        M4A\n        North York\n   
4        M5A\n  Downtown Toronto\n   
..         ...                 ...   
175      M5Z\n      Not assigned\n   
176      M6Z\n      Not assigned\n   
177      M7Z\n      Not assigned\n   
178      M8Z\n         Etobicoke\n   
179      M9Z\n      Not assigned\n   

                                          Neighborhood  
0                                                   \n  
1                                                   \n  
2                                          Parkwoods\n  
3                                   Victoria Village\n  
4                         Regent Park / Harbourfront\n  
..                                                 ...  
175                                                 \n  
176                                                 \n  
177                                                 \n  
178  Mimico NW / The Queensway West / South of Bloo...  
179                                                 \n  

[180 rows x 3 columns]

In [5]:
#data frame cleaning by removin the '\n' using  REGEX: 
import re
for index,row in df_table.iterrows():
    for col in df_table.columns:
        row[col]= re.sub(r'\n','',row[col])
df_table

PostalCode           Borough  \
0          M1A      Not assigned   
1          M2A      Not assigned   
2          M3A        North York   
3          M4A        North York   
4          M5A  Downtown Toronto   
..         ...               ...   
175        M5Z      Not assigned   
176        M6Z      Not assigned   
177        M7Z      Not assigned   
178        M8Z         Etobicoke   
179        M9Z      Not assigned   

                                          Neighborhood  
0                                                       
1                                                       
2                                            Parkwoods  
3                                     Victoria Village  
4                           Regent Park / Harbourfront  
..                                                 ...  
175                                                     
176                                                     
177                                                     
178  Mimico NW / The Queensway West / South of Bloo...  
179                                                     

[180 rows x 3 columns]

In [7]:
#drop rows where no borough were attributed and copy borough neighborhood where no neighborood
for index, row in df_table.iterrows():
    row['Neighborhood']=row['Neighborhood'].replace('/',',')
    if row['Borough']=='Not assigned':
        df_table.drop([index],inplace=True)
    if row['Neighborhood']== '':
        row['Neighborhood']=row['Borough']
df_table.reset_index(inplace=True,drop=True)
df_table.head(15)

PostalCode           Borough  \
0         M3A        North York   
1         M4A        North York   
2         M5A  Downtown Toronto   
3         M6A        North York   
4         M7A  Downtown Toronto   
5         M9A         Etobicoke   
6         M1B       Scarborough   
7         M3B        North York   
8         M4B         East York   
9         M5B  Downtown Toronto   
10        M6B        North York   
11        M9B         Etobicoke   
12        M1C       Scarborough   
13        M3C        North York   
14        M4C         East York   

                                         Neighborhood  
0                                           Parkwoods  
1                                    Victoria Village  
2                          Regent Park , Harbourfront  
3                   Lawrence Manor , Lawrence Heights  
4        Queen's Park , Ontario Provincial Government  
5                                    Islington Avenue  
6                                     Malvern , Rouge  
7                                           Don Mills  
8                    Parkview Hill , Woodbine Gardens  
9                            Garden District, Ryerson  
10                                          Glencairn  
11  West Deane Park , Princess Gardens , Martin Gr...  
12           Rouge Hill , Port Union , Highland Creek  
13                                          Don Mills  
14                                   Woodbine Heights

In [8]:
# checking if any null values are stil in the data frame : 
df_clean=df_table.isnull()
for column in df_clean.columns: 
    print(column)
    print(df_clean[column].value_counts())

PostalCode
False    103
Name: PostalCode, dtype: int64
Borough
False    103
Name: Borough, dtype: int64
Neighborhood
False    103
Name: Neighborhood, dtype: int64


In [9]:
df_table.shape

(103, 3)

In [134]:
#export data to csv
import csv
#df_table.to_csv('postal_code.csv')

# 2. Adding coordinates of neighborhoods <a id="2"></a>


In [11]:
# instal of geocoder 
#!pip install geocoder

In [2]:
import geocoder # import geocoder

In [15]:
# initialize your variable to None
lat_lng_coords = None
for index,code in enumerate(df_table['PostalCode']): 
    postal_code=code
    print(index, 'st row to complete')
# loop until you get the coordinates
    while(lat_lng_coords is None):
        g = geocoder.geocodefarm('{}, Toronto, Ontario,Canada'.format(postal_code))
        lat_lng_coords = g.latlng
        print(lat_lng_coords)
    df_table.at[index,'latitude'] = lat_lng_coords[0]
    df_table.at[index,'longitude'] = lat_lng_coords[1]
    print(index, 'st row completed')
    lat_lng_coords = None

0 st row to complete
[43.7518806457716, -79.3303604125129]
0 st row completed
1 st row to complete
[43.7304191589716, -79.3128204341299]
1 st row completed
2 st row to complete
None
None
[43.6551399230715, -79.362648010213]
2 st row completed
3 st row to complete
[43.7232093811716, -79.4514083861301]
3 st row completed
4 st row to complete
None
[43.6644897460715, -79.393020629813]
4 st row completed
5 st row to complete
[43.6627693176715, -79.528312683113]
5 st row completed
6 st row to complete


KeyboardInterrupt: 

In [253]:
# extraction of the dataframe into a csv file
#df_table.to_csv('postal_code.csv')

# 3. Folium Maps <a id="3"></a>

In [3]:
#reading the previously completed csv with cordinates
df_table=pd.read_csv('postal_code.csv',index_col=0)
df_table

PostalCode           Borough  \
0          M3A        North York   
1          M4A        North York   
2          M5A  Downtown Toronto   
3          M6A        North York   
4          M7A  Downtown Toronto   
..         ...               ...   
98         M8X         Etobicoke   
99         M4Y  Downtown Toronto   
100        M7Y      East Toronto   
101        M8Y         Etobicoke   
102        M8Z         Etobicoke   

                                          Neighborhood   latitude  longitude  
0                                            Parkwoods  43.751881 -79.330360  
1                                     Victoria Village  43.730419 -79.312820  
2                           Regent Park , Harbourfront  43.655140 -79.362648  
3                    Lawrence Manor , Lawrence Heights  43.723209 -79.451408  
4         Queen's Park , Ontario Provincial Government  43.664490 -79.393021  
..                                                 ...        ...        ...  
98    The Kingsway , Montgomery Road  , Old Mill North  43.653690 -79.511124  
99                                Church and Wellesley  43.666592 -79.381302  
100              Business reply mail Processing CentrE  43.648689 -79.385437  
101  Old Mill South , King's Mill Park , Sunnylea ,...  43.632881 -79.489548  
102  Mimico NW , The Queensway West , South of Bloo...  43.624630 -79.528351  

[103 rows x 5 columns]

In [4]:
#checking data with folium maps of neigborhoods
#1st coordinates of Toronto
g2 = geocoder.geocodefarm('Toronto, Ontario,Canada')
latlong= g2.latlng
latitude= latlong[0]
longitude = latlong[1]
print(f'latitude {latitude} & longitude {longitude}')

latitude 43.6486892707151 & longitude -79.385437011713


In [5]:
#folium map : 
toronto_map= folium.Map(location=[latitude, longitude],tiles='OpenStreetMap', zoom_start=10)
for borough,neighborhood, lat,long in zip(df_table['Borough'],df_table['Neighborhood'],df_table['latitude'],df_table['longitude']):
    label=(f'{borough}, {neighborhood}')
    label=folium.Popup(label,parse_html=True)
    folium.CircleMarker(location=[lat,long],
                        popup=label,
                        radius=5, 
                        fill=True,
                        fill_color='#3388ff',
                        fill_opacity=1,
                        parse_html=False).add_to(toronto_map)
    
toronto_map

# 4. Cluster neighborhoods<a id="4"></a>

In [9]:
#import librairies : 
# library to handle JSON files
import json 
 # library to handle requests
import requests 
from sklearn.cluster import KMeans
# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

In [10]:
#GET INFORMATION ON FOURSQUARE API
#FOURSQUARE CREDENTIALS
CLIENT_ID = 'CUF5UKNECLDYIDGLLSJJF32FI1RYQJBR1WRLHIFQEVRSJJO4' 
CLIENT_SECRET = 'SW40I4VDCJKKBFFXLQOFRMBRW0AQ1DWO3ZO23QF3JUXLKWFJ' 
VERSION = '20180605' 

print('Credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

#foursquare url : 
url_base='https://api.foursquare.com/v2/'

Credentails:
CLIENT_ID: CUF5UKNECLDYIDGLLSJJF32FI1RYQJBR1WRLHIFQEVRSJJO4
CLIENT_SECRET:SW40I4VDCJKKBFFXLQOFRMBRW0AQ1DWO3ZO23QF3JUXLKWFJ


In [11]:
Toronto_data=pd.DataFrame(columns=df_table.columns[1:])

In [12]:
for index,row in enumerate(df_table['Borough']):
    if 'Toronto' in row: 
        Toronto_data=Toronto_data.append(df_table.loc[index,'Borough':'longitude'])
Toronto_data.reset_index(inplace=True,drop=True)

In [13]:
Toronto_data

Borough                                       Neighborhood  \
0   Downtown Toronto                         Regent Park , Harbourfront   
1   Downtown Toronto       Queen's Park , Ontario Provincial Government   
2   Downtown Toronto                           Garden District, Ryerson   
3   Downtown Toronto                                     St. James Town   
4       East Toronto                                        The Beaches   
5   Downtown Toronto                                        Berczy Park   
6   Downtown Toronto                                 Central Bay Street   
7   Downtown Toronto                                           Christie   
8   Downtown Toronto                         Richmond , Adelaide , King   
9       West Toronto                      Dufferin , Dovercourt Village   
10  Downtown Toronto  Harbourfront East , Union Station , Toronto Is...   
11      West Toronto                          Little Portugal , Trinity   
12      East Toronto                      The Danforth West , Riverdale   
13  Downtown Toronto          Toronto Dominion Centre , Design Exchange   
14      West Toronto     Brockton , Parkdale Village , Exhibition Place   
15      East Toronto                    India Bazaar , The Beaches West   
16  Downtown Toronto                    Commerce Court , Victoria Hotel   
17      East Toronto                                    Studio District   
18   Central Toronto                                      Lawrence Park   
19   Central Toronto                                           Roselawn   
20   Central Toronto                                   Davisville North   
21   Central Toronto                           Forest Hill North & West   
22      West Toronto                     High Park , The Junction South   
23   Central Toronto                                 North Toronto West   
24   Central Toronto              The Annex , North Midtown , Yorkville   
25      West Toronto                            Parkdale , Roncesvalles   
26   Central Toronto                                         Davisville   
27  Downtown Toronto                    University of Toronto , Harbord   
28      West Toronto                                Runnymede , Swansea   
29   Central Toronto                       Moore Park , Summerhill East   
30  Downtown Toronto        Kensington Market , Chinatown , Grange Park   
31   Central Toronto  Summerhill West , Rathnelly , South Hill , For...   
32  Downtown Toronto  CN Tower , King and Spadina , Railway Lands , ...   
33  Downtown Toronto                                           Rosedale   
34  Downtown Toronto                                     Stn A PO Boxes   
35  Downtown Toronto                       St. James Town , Cabbagetown   
36  Downtown Toronto            First Canadian Place , Underground city   
37  Downtown Toronto                               Church and Wellesley   
38      East Toronto              Business reply mail Processing CentrE   

     latitude  longitude  
0   43.655140 -79.362648  
1   43.664490 -79.393021  
2   43.657360 -79.378181  
3   43.651428 -79.375572  
4   43.677029 -79.295418  
5   43.645309 -79.373680  
6   43.656090 -79.384933  
7   43.668781 -79.420708  
8   43.649700 -79.382584  
9   43.665089 -79.438713  
10  43.642849 -79.380402  
11  43.648731 -79.417839  
12  43.683750 -79.355278  
13  43.647099 -79.381531  
14  43.639408 -79.426758  
15  43.667969 -79.314682  
16  43.648232 -79.378899  
17  43.660912 -79.335030  
18  43.728981 -79.391731  
19  43.711941 -79.419121  
20  43.712761 -79.388512  
21  43.694790 -79.414398  
22  43.659939 -79.463020  
23  43.714520 -79.406960  
24  43.674839 -79.401848  
25  43.647850 -79.450203  
26  43.703400 -79.385963  
27  43.663109 -79.401802  
28  43.650341 -79.475708  
29  43.690659 -79.383560  
30  43.653511 -79.397217  
31  43.685692 -79.402321  
32  43.640820 -79.399559  
33  43.681900 -79.378502  
34  43.648689 -79.385437  
35  43.667881 -79.366493  
36  43.648281

In [14]:
# visualisation of Toronto Boroughs : 

borough= folium.Map(location=[latitude,longitude],zoom_start=11)
for lat,long,bo,nei in zip(Toronto_data['latitude'],Toronto_data['longitude'],Toronto_data['Borough'],Toronto_data['Neighborhood']):
    label=(bo +' -\n'+ nei)
    label=folium.Popup(label, parse_html=True)
    folium.CircleMarker(location=[lat,long],
                        popup=label,
                        radius=5,
                        fill=True,
                        fill_color='#3388ff',
                        fill_opacity=1,
                        parse_html=False
                       ).add_to(borough)
borough

In [27]:
# connect to foursquare and get the venues for all neigborhoods
RADIUS=500
LIMIT= 100
temp=pd.DataFrame()
all_toronto_venues = pd.DataFrame(columns=['PostalCode', 'Borough', 'Neighborhood', 'latitude', 'longitude','venu_name','venue_category'])
for code, bo, nei,lat,long in zip(df_table['PostalCode'],df_table['Borough'],df_table['Neighborhood'],df_table['latitude'],df_table['longitude']):
    url=url_base+f'venues/explore?&client_id={CLIENT_ID}&client_secret={CLIENT_SECRET}&v={VERSION}&ll={lat},{long}&radius={RADIUS}&limit={LIMIT}'
    results=requests.get(url).json()    
    for i in range(len(results['response']['groups'][0]['items'])):
        temp.at[i,'PostalCode']=code
        temp.at[i,'Borough']=bo
        temp.at[i,'Neighborhood']=nei
        temp.at[i,'latitude']=lat
        temp.at[i,'longitude']=long
        temp.at[i,'venu_name']=results['response']['groups'][0]['items'][i]['venue']['name']
        temp.at[i,'venue_category']=results['response']['groups'][0]['items'][i]['venue']['categories'][0]['name']
    all_toronto_venues=all_toronto_venues.append(temp,ignore_index=True)
all_toronto_venues

PostalCode       Borough                           Neighborhood  \
0           M3A    North York                              Parkwoods   
1           M3A    North York                              Parkwoods   
2           M3A    North York                              Parkwoods   
3           M4A    North York                       Victoria Village   
4           M4A    North York                       Victoria Village   
...         ...           ...                                    ...   
9749        M7Y  East Toronto  Business reply mail Processing CentrE   
9750        M7Y  East Toronto  Business reply mail Processing CentrE   
9751        M7Y  East Toronto  Business reply mail Processing CentrE   
9752        M7Y  East Toronto  Business reply mail Processing CentrE   
9753        M7Y  East Toronto  Business reply mail Processing CentrE   

       latitude  longitude                                  venu_name  \
0     43.751881 -79.330360                            Brookbanks Park   
1     43.751881 -79.330360                                   PetSmart   
2     43.751881 -79.330360                              Variety Store   
3     43.730419 -79.312820                         Memories of Africa   
4     43.730419 -79.312820  Eglinton Ave E & Sloane Ave/Bermondsey Rd   
...         ...        ...                                        ...   
9749  43.648689 -79.385437                                 Mr Burrito   
9750  43.648689 -79.385437                         Rexall Pharma Plus   
9751  43.648689 -79.385437                                 Ematei 絵馬亭   
9752  43.648689 -79.385437               Meli Baklava & Chocolate Bar   
9753  43.648689 -79.385437                           Red Eye Espresso   

           venue_category  
0                    Park  
1               Pet Store  
2       Food & Drink Shop  
3           Grocery Store  
4            Intersection  
...                   ...  
9749        Burrito Place  
9750             Pharmacy  
9751  Japanese Restaurant  
9752       Chocolate Shop  
9753                 Café  

[9754 rows x 7 columns]

In [33]:
all_toronto_venues

PostalCode           Borough  \
0           M3A        North York   
1           M3A        North York   
2           M3A        North York   
3           M4A        North York   
4           M4A        North York   
5           M3A        North York   
6           M5A  Downtown Toronto   
7           M5A  Downtown Toronto   
8           M5A  Downtown Toronto   
9           M5A  Downtown Toronto   
10          M5A  Downtown Toronto   
11          M5A  Downtown Toronto   
12          M5A  Downtown Toronto   
13          M5A  Downtown Toronto   
14          M5A  Downtown Toronto   
15          M5A  Downtown Toronto   
16          M5A  Downtown Toronto   
17          M5A  Downtown Toronto   
18          M5A  Downtown Toronto   
19          M5A  Downtown Toronto   
20          M5A  Downtown Toronto   
21          M5A  Downtown Toronto   
22          M5A  Downtown Toronto   
23          M5A  Downtown Toronto   
24          M5A  Downtown Toronto   
25          M5A  Downtown Toronto   
26          M5A  Downtown Toronto   
27          M5A  Downtown Toronto   
28          M5A  Downtown Toronto   
29          M5A  Downtown Toronto   
30          M6A        North York   
31          M6A        North York   
32          M6A        North York   
33          M6A        North York   
34          M6A        North York   
35          M6A        North York   
36          M6A        North York   
37          M6A        North York   
38          M6A        North York   
39          M6A        North York   
40          M6A        North York   
41          M6A        North York   
42          M6A        North York   
43          M6A        North York   
44          M6A        North York   
45          M6A        North York   
46          M6A        North York   
47          M6A        North York   
48          M6A        North York   
49          M6A        North York   
50          M6A        North York   
51          M6A        North York   
52          M6A        North York   
53          M6A        North York   
54          M6A        North York   
55          M6A        North York   
56          M6A        North York   
57          M6A        North York   
58          M6A        North York   
59          M6A        North York   
60          M6A        North York   
61          M6A        North York   
62          M6A        North York   
63          M6A        North York   
64          M6A        North York   
65          M6A        North York   
66          M6A        North York   
67          M6A        North York   
68          M6A        North York   
69          M6A        North York   
70          M6A        North York   
71          M6A        North York   
72          M6A        North York   
73          M6A        North York   
74          M6A        North York   
75          M6A        North York   
76          M6A        North York   
77          M6A        North York   
78          M6A        North York   
79          M6A        North York   
80          M6A        North York   
81          M6A        North York   
82          M6A        North York   
83          M6A        North York   
84          M7A  Downtown Toronto   
85          M7A  Downtown Toronto   
86          M7A  Downtown Toronto   
87          M7A  Downtown Toronto   
88          M7A  Downtown Toronto   
89          M7A  Downtown Toronto   
90          M7A  Downtown Toronto   
91          M7A  Downtown Toronto   
92          M7A  Downtown Toronto   
93          M7A  Downtown Toronto   
94          M7A  Downtown Toronto   
95          M7A  Downtown Toronto   
96          M7A  Downtown Toronto   
97          M7A  Downtown Toronto   
98          M7A  Downtown Toronto   
99          M7A  Downtown Toronto   
100         M7A  Downtown Toronto   
101         M7A  Downtown Toronto   
102         M7A  Downtown Toronto   
103         M7A  Downtown Toronto   
104         M7A  Downtown Toronto   
105         M7A  Downtown Toronto   
106         M7A  Downtown Toronto   
107      

In [48]:
# group by neighborhoods the most venues category 
dummies=pd.get_dummies(all_toronto_venues[['venue_category']], prefix="", prefix_sep="")
dummies['Neighborhood']=all_toronto_venues['Neighborhood']
#getting last column at the bigining (neigborhoods):
ordered_columns=[dummies.columns[-1]]+ list(dummies.columns[:-1])
dummies=dummies[ordered_columns]
dummies
all_toronto_grouped=dummies.groupby('Neighborhood').mean().reset_index()
all_toronto_grouped.head()

Neighborhood  Yoga Studio  ATM  Accessories Store  \
0                           Agincourt     0.000000  0.0                0.0   
1             Alderwood , Long Branch     0.000000  0.0                0.0   
2                     Bayview Village     0.000000  0.0                0.0   
3  Bedford Park , Lawrence Manor East     0.000000  0.0                0.0   
4                         Berczy Park     0.013841  0.0                0.0   

   Adult Boutique  Airport  American Restaurant  Antique Shop  Aquarium  \
0             0.0      0.0                  0.0           0.0       0.0   
1             0.0      0.0                  0.0           0.0       0.0   
2             0.0      0.0                  0.0           0.0       0.0   
3             0.0      0.0                  0.0           0.0       0.0   
4             0.0      0.0                  0.0           0.0       0.0   

   Art Gallery  Art Museum  Arts & Crafts Store  Asian Restaurant  \
0     0.000000         0.0                  0.0               0.0   
1     0.000000         0.0                  0.0               0.0   
2     0.000000         0.0                  0.0               0.0   
3     0.000000         0.0                  0.0               0.0   
4     0.010381         0.0                  0.0               0.0   

   Athletics & Sports  Auto Dealership  Auto Garage  BBQ Joint  Baby Store  \
0                 0.0              0.0          0.0   0.000000         0.0   
1                 0.0              0.0          0.0   0.000000         0.0   
2                 0.0              0.0          0.0   0.000000         0.0   
3                 0.0              0.0          0.0   0.000000         0.0   
4                 0.0              0.0          0.0   0.013841         0.0   

   Badminton Court  Bagel Shop    Bakery  Bank  Bar  Baseball Field  \
0            0.125    0.000000  0.000000   0.0  0.0             0.0   
1            0.000    0.000000  0.000000   0.0  0.0             0.0   
2            0.000    0.000000  0.000000   0.0  0.0             0.0   
3            0.000    0.000000  0.000000   0.0  0.0             0.0   
4            0.000    0.013841  0.024221   0.0  0.0             0.0   

   Basketball Stadium  Beer Bar  Beer Store  Belgian Restaurant  Bike Shop  \
0            0.000000  0.000000         0.0                 0.0        0.0   
1            0.000000  0.000000         0.0                 0.0        0.0   
2            0.000000  0.000000         0.0                 0.0        0.0   
3            0.000000  0.000000         0.0                 0.0        0.0   
4            0.010381  0.020761         0.0                 0.0        0.0   

     Bistro  Boat or Ferry  Bookstore  Boutique  Brazilian Restaurant  \
0  0.000000            0.0        0.0       0.0                   0.0   
1  0.000000            0.0        0.0       0.0                   0.0   
2  0.000000            0.0        0.0       0.0                   0.0   
3  0.000000            0.0        0.0       0.0                   0.0   
4  0.010381            0.0        0.0       0.0                   0.0   

   Breakfast Spot  Brewery  Bridge  Bubble Tea Shop  Building  Burger Joint  \
0        0.000000      0.0     0.0              0.0       0.0           0.0   
1        0.000000      0.0     0.0              0.0       0.0           0.0   
2        0.000000      0.0     0.0              0.0       0.0           0.0   
3        0.000000      0.0     0.0              0.0       0.0           0.0   
4        0.034602      0.0     0.0              0.0       0.0           0.0   

   Burrito Place  Bus Line  Bus Station  Bus Stop  Business Service   Butcher  \
0            0.0       0.0          0.0       0.0               0.0  0.000000   
1            0.0       0.0          0.0       0.0               0.0  0.000000   
2            0.0       0.0          0.0       0.0               0.0  0.000000   
3            0.0       0.0          0.0       0.0               0.0  0.064516   
4     

In [51]:
# keep the 10 most present venues per neighborhoods
#sort the venues :
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)

    return row_categories_sorted.index.values[0:num_top_venues] 


In [52]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = all_toronto_grouped['Neighborhood']

for ind in np.arange(all_toronto_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(all_toronto_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue  \
0                           Agincourt       Badminton Court   
1             Alderwood , Long Branch           Pizza Place   
2                     Bayview Village                 Trail   
3  Bedford Park , Lawrence Manor East    Italian Restaurant   
4                         Berczy Park           Coffee Shop   

        2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0            Sushi Restaurant                  Park          Skating Rink   
1                         Gym        Sandwich Place     Convenience Store   
2  Construction & Landscaping                  Park    Golf Driving Range   
3              Sandwich Place           Coffee Shop          Liquor Store   
4          Seafood Restaurant            Restaurant                Lounge   

  5th Most Common Venue 6th Most Common Venue  7th Most Common Venue  \
0         Shopping Mall                  Pool         Discount Store   
1                   Pub                  Farm         Farmers Market   
2           Event Space            Donut Shop    Dumpling Restaurant   
3           Sports Club               Butcher              Juice Bar   
4    Italian Restaurant            Steakhouse  Portuguese Restaurant   

         8th Most Common Venue        9th Most Common Venue  \
0                  Supermarket  Eastern European Restaurant   
1           Falafel Restaurant                  Event Space   
2  Eastern European Restaurant            Electronics Store   
3             Sushi Restaurant                          Pub   
4         Fast Food Restaurant               Breakfast Spot   

    10th Most Common Venue  
0                  Dog Run  
1           Discount Store  
2     Ethiopian Restaurant  
3  Comfort Food Restaurant  
4            Movie Theater

In [102]:
# apply clustering algorithm on neighborhoods based on most common categories 
k=5

all_toronto_grouped_clustering = all_toronto_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=k, n_init=15, random_state=0).fit(all_toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([1, 1, 0, 1, 1, 1, 1, 1, 1, 1])

In [103]:
# add clustering labels
try : 
    neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)
except: 
    neighborhoods_venues_sorted.drop(columns='Cluster Labels',inplace=True)
    neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

toronto_merged = df_table

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
toronto_merged = toronto_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

toronto_merged.head() # check the last columns!

PostalCode           Borough                                  Neighborhood  \
0        M3A        North York                                     Parkwoods   
1        M4A        North York                              Victoria Village   
2        M5A  Downtown Toronto                    Regent Park , Harbourfront   
3        M6A        North York             Lawrence Manor , Lawrence Heights   
4        M7A  Downtown Toronto  Queen's Park , Ontario Provincial Government   

    latitude  longitude  Cluster Labels 1st Most Common Venue  \
0  43.751881 -79.330360             3.0     Food & Drink Shop   
1  43.730419 -79.312820             1.0          Intersection   
2  43.655140 -79.362648             1.0           Coffee Shop   
3  43.723209 -79.451408             1.0        Clothing Store   
4  43.664490 -79.393021             1.0           Coffee Shop   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0                  Park             Pet Store           Event Space   
1         Grocery Store         Women's Store           Event Space   
2        Breakfast Spot           Yoga Studio                Bakery   
3             Bookstore         Women's Store      Toy / Game Store   
4                  Café           Music Store                   Pub   

    5th Most Common Venue 6th Most Common Venue        7th Most Common Venue  \
0              Donut Shop   Dumpling Restaurant  Eastern European Restaurant   
1              Donut Shop   Dumpling Restaurant  Eastern European Restaurant   
2       Health Food Store    Italian Restaurant                   Food Truck   
3  Furniture / Home Store           Men's Store                   Restaurant   
4               Hotel Bar     Convenience Store               Sandwich Place   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0     Electronics Store  Ethiopian Restaurant          Women's Store  
1     Electronics Store  Ethiopian Restaurant     Falafel Restaurant  
2           Event Space     Electronics Store     Mexican Restaurant  
3              Pharmacy   American Restaurant                   Café  
4           Salad Place        Clothing Store     Chinese Restaurant

In [104]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 0, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue  \
26       Scarborough             0.0                 Trail   
35         East York             0.0            Playground   
39        North York             0.0                 Trail   
73   Central Toronto             0.0            Playground   
83   Central Toronto             0.0                 Trail   
91  Downtown Toronto             0.0            Playground   

         2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
26                  Playground         Women's Store               Dog Run   
35                 Music Venue                  Park  Fast Food Restaurant   
39  Construction & Landscaping                  Park    Golf Driving Range   
73                    Gym Pool                  Park                Garden   
83                  Playground                   Gym                  Park   
91                Tennis Court              Building                  Park   

   5th Most Common Venue 6th Most Common Venue        7th Most Common Venue  \
26            Donut Shop   Dumpling Restaurant  Eastern European Restaurant   
35        Farmers Market                  Farm           Falafel Restaurant   
39           Event Space            Donut Shop          Dumpling Restaurant   
73        Farmers Market                  Farm           Falafel Restaurant   
83  Ethiopian Restaurant   Distribution Center                      Dog Run   
91         Women's Store     Electronics Store                      Dog Run   

          8th Most Common Venue 9th Most Common Venue  \
26            Electronics Store  Ethiopian Restaurant   
35                  Event Space  Ethiopian Restaurant   
39  Eastern European Restaurant     Electronics Store   
73                  Event Space        Discount Store   
83                   Donut Shop   Dumpling Restaurant   
91                   Donut Shop   Dumpling Restaurant   

         10th Most Common Venue  
26                  Event Space  
35            Electronics Store  
39         Ethiopian Restaurant  
73         Fast Food Restaurant  
83  Eastern European Restaurant  
91  Eastern European Restaurant

In [105]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 1, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels  \
1          North York             1.0   
2    Downtown Toronto             1.0   
3          North York             1.0   
4    Downtown Toronto             1.0   
5           Etobicoke             1.0   
7          North York             1.0   
8           East York             1.0   
9    Downtown Toronto             1.0   
10         North York             1.0   
13         North York             1.0   
14          East York             1.0   
15   Downtown Toronto             1.0   
17          Etobicoke             1.0   
19       East Toronto             1.0   
20   Downtown Toronto             1.0   
21               York             1.0   
22        Scarborough             1.0   
23          East York             1.0   
24   Downtown Toronto             1.0   
25   Downtown Toronto             1.0   
27         North York             1.0   
29          East York             1.0   
30   Downtown Toronto             1.0   
31       West Toronto             1.0   
32        Scarborough             1.0   
33         North York             1.0   
34         North York             1.0   
36   Downtown Toronto             1.0   
37       West Toronto             1.0   
38        Scarborough             1.0   
40         North York             1.0   
41       East Toronto             1.0   
42   Downtown Toronto             1.0   
43       West Toronto             1.0   
44        Scarborough             1.0   
46         North York             1.0   
47       East Toronto             1.0   
48   Downtown Toronto             1.0   
50         North York             1.0   
51        Scarborough             1.0   
52         North York             1.0   
53         North York             1.0   
54       East Toronto             1.0   
55         North York             1.0   
56               York             1.0   
57         North York             1.0   
58        Scarborough             1.0   
59         North York             1.0   
60         North York             1.0   
63               York             1.0   
64               York             1.0   
65        Scarborough             1.0   
66         North York             1.0   
67    Central Toronto             1.0   
70          Etobicoke             1.0   
71        Scarborough             1.0   
72         North York             1.0   
74    Central Toronto             1.0   
75       West Toronto             1.0   
76        Mississauga             1.0   
77          Etobicoke             1.0   
78        Scarborough             1.0   
79    Central Toronto             1.0   
80   Downtown Toronto             1.0   
81       West Toronto             1.0   
82        Scarborough             1.0   
84   Downtown Toronto             1.0   
85        Scarborough             1.0   
86    Central Toronto             1.0   
87   Downtown Toronto             1.0   
89          Etobicoke             1.0   
90        Scarborough             1.0   
92   Downtown Toronto             1.0   
93          Etobicoke             1.0   
94          Etobicoke             1.0   
96   Downtown Toronto             1.0   
97   Downtown Toronto             1.0   
99   Downtown Toronto             1.0   
100      East Toronto             1.0   
101         Etobicoke             1.0   
102         Etobicoke             1.0   

                        1st Most Common Venue      2nd Most Common Venue  \
1                                Intersection              Grocery Store   
2                                 Coffee Shop             Breakfast Spot   
3                              Clothing Store                  Bookstore   
4                                 Coffee Shop                       Café   
5                                    Pharmacy               Skating Rink   
7                                 Coffee Shop               Intersection   
8                                 Pizza Place       Fast Food Restaurant   
9                                 Coffee Sh

In [106]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 2, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
11  Etobicoke             2.0         Movie Theater         Women's Store   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
11            Comic Shop     Fish & Chips Shop                 Field   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
11  Fast Food Restaurant        Farmers Market                  Farm   

   9th Most Common Venue 10th Most Common Venue  
11    Falafel Restaurant            Event Space

In [107]:
toronto_merged.loc[toronto_merged['Cluster Labels'] ==3, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels                     1st Most Common Venue  \
0        North York             3.0                         Food & Drink Shop   
16             York             3.0                                     Trail   
18      Scarborough             3.0                Construction & Landscaping   
49       North York             3.0                                      Park   
61  Central Toronto             3.0                                      Park   
68  Central Toronto             3.0                                Restaurant   
69     West Toronto             3.0  Residential Building (Apartment / Condo)   
88        Etobicoke             3.0                                      Park   
98        Etobicoke             3.0                                      Park   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0                   Park             Pet Store           Event Space   
16                 Field          Hockey Arena         Grocery Store   
18  Gym / Fitness Center                  Park         Women's Store   
49                Bakery           Event Space            Donut Shop   
61    Dim Sum Restaurant           Event Space            Donut Shop   
68                  Park         Women's Store  Ethiopian Restaurant   
69                  Park         Women's Store  Ethiopian Restaurant   
88           Yoga Studio                   ATM          Tennis Court   
98                  Pool           Event Space               Dog Run   

   5th Most Common Venue        6th Most Common Venue  \
0             Donut Shop          Dumpling Restaurant   
16                  Park         Ethiopian Restaurant   
18           Event Space                   Donut Shop   
49   Dumpling Restaurant  Eastern European Restaurant   
61   Dumpling Restaurant  Eastern European Restaurant   
68               Dog Run                   Donut Shop   
69               Dog Run                   Donut Shop   
88          Skating Rink                Grocery Store   
98            Donut Shop          Dumpling Restaurant   

          7th Most Common Venue        8th Most Common Venue  \
0   Eastern European Restaurant            Electronics Store   
16                      Dog Run                   Donut Shop   
18          Dumpling Restaurant  Eastern European Restaurant   
49            Electronics Store         Ethiopian Restaurant   
61            Electronics Store         Ethiopian Restaurant   
68          Dumpling Restaurant  Eastern European Restaurant   
69          Dumpling Restaurant  Eastern European Restaurant   
88            Electronics Store                      Dog Run   
98  Eastern European Restaurant            Electronics Store   

   9th Most Common Venue       10th Most Common Venue  
0   Ethiopian Restaurant                Women's Store  
16   Dumpling Restaurant  Eastern European Restaurant  
18     Electronics Store         Ethiopian Restaurant  
49         Women's Store          Distribution Center  
61         Women's Store          Distribution Center  
68     Electronics Store                  Event Space  
69     Electronics Store                  Event Space  
88            Donut Shop          Dumpling Restaurant  
98  Ethiopian Restaurant                Women's Store

In [108]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 4, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Borough  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
12  Scarborough             4.0        History Museum                   Bar   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
12               Dog Run           Fish Market     Fish & Chips Shop   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
12                 Field  Fast Food Restaurant        Farmers Market   

   9th Most Common Venue 10th Most Common Venue  
12                  Farm     Falafel Restaurant

In [109]:
# initialize the plot with the specified dimensions.
fig = plt.figure(figsize=(15, 10))

# colors uses a color map, which will produce an array of colors based on
# the number of labels. We use set(k_means_labels) to get the
# unique labels.
colors = plt.cm.Spectral(np.linspace(0, 1, len(set(k_means_labels))))

# create a plot
ax = fig.add_subplot(1, 1, 1)

# loop through the data and plot the datapoints and centroids.
# k will range from 0-3, which will match the number of clusters in the dataset.
for k, col in zip(range(len([[4,4], [-2, -1], [2, -3], [1, 1]])), colors):

    # create a list of all datapoints, where the datapoitns that are 
    # in the cluster (ex. cluster 0) are labeled as true, else they are
    # labeled as false.
    my_members = (k_means_labels == k)
    
    # define the centroid, or cluster center.
    cluster_center = k_means_cluster_centers[k]
    
    # plot the datapoints with color col.
    ax.plot(X[my_members, 0], X[my_members, 1], 'w', markerfacecolor=col, marker='.')
    
    # plot the centroids with specified color, but with a darker outline
    ax.plot(cluster_center[0], cluster_center[1], 'o', markerfacecolor=col,  markeredgecolor='k', markersize=6)

# title of the plot
ax.set_title('KMeans')

# remove x-axis ticks
ax.set_xticks(())

# remove y-axis ticks
ax.set_yticks(())

# show the plot
plt.show()

PostalCode           Borough                                  Neighborhood  \
0        M3A        North York                                     Parkwoods   
1        M4A        North York                              Victoria Village   
2        M5A  Downtown Toronto                    Regent Park , Harbourfront   
3        M6A        North York             Lawrence Manor , Lawrence Heights   
4        M7A  Downtown Toronto  Queen's Park , Ontario Provincial Government   

    latitude  longitude  Cluster Labels 1st Most Common Venue  \
0  43.751881 -79.330360             3.0     Food & Drink Shop   
1  43.730419 -79.312820             1.0          Intersection   
2  43.655140 -79.362648             1.0           Coffee Shop   
3  43.723209 -79.451408             1.0        Clothing Store   
4  43.664490 -79.393021             1.0           Coffee Shop   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0                  Park             Pet Store           Event Space   
1         Grocery Store         Women's Store           Event Space   
2        Breakfast Spot           Yoga Studio                Bakery   
3             Bookstore         Women's Store      Toy / Game Store   
4                  Café           Music Store                   Pub   

    5th Most Common Venue 6th Most Common Venue        7th Most Common Venue  \
0              Donut Shop   Dumpling Restaurant  Eastern European Restaurant   
1              Donut Shop   Dumpling Restaurant  Eastern European Restaurant   
2       Health Food Store    Italian Restaurant                   Food Truck   
3  Furniture / Home Store           Men's Store                   Restaurant   
4               Hotel Bar     Convenience Store               Sandwich Place   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0     Electronics Store  Ethiopian Restaurant          Women's Store  
1     Electronics Store  Ethiopian Restaurant     Falafel Restaurant  
2           Event Space     Electronics Store     Mexican Restaurant  
3              Pharmacy   American Restaurant                   Café  
4           Salad Place        Clothing Store     Chinese Restaurant

# Code pour boucler sur le dataframe et fusionner les neighborhoods ayant les mêmes code postals 

In [242]:
df_test=df_table[['PostalCode','Borough','Neighborhood']].copy()
#ajout de deux lignes supplémentaires avec même code postal pour l'exercice : 
df_test=df_test.append(pd.DataFrame({'PostalCode':['M3A','M3A'],'Borough':['North York','North York'],'Neighborhood':['Pierre','Sarah']}))
df_test.reset_index(inplace=True,drop=True)

In [243]:
#on trie les valeurs pour que les codes postaux identiques soient à la suite dans le data frame : 
df_test=df_test.sort_values(by=['PostalCode'])
df_test.reset_index(inplace=True,drop=True)
# Boucle pour trouver les codes postals identiques et fusionner les neigborhoods: 
for index, value in enumerate(df_test['PostalCode']):
    try : 
        i=1
        if index!= len(df_test['PostalCode']) :
            while value == df_test.loc[index+i, 'PostalCode']:  
                df_test.at[index,'Neighborhood']+= ', '+ (df_test.at[index+i,'Neighborhood'])
                df_test.drop([index+i],inplace=True)
                i+=1     
    except : 
        print('fin du dataframe')
                       

fin du dataframe
fin du dataframe


In [244]:
df_test[df_test['PostalCode']=='M3A']

PostalCode     Borough              Neighborhood
25        M3A  North York  Pierre, Parkwoods, Sarah

In [210]:
df_test

PostalCode      Borough                                       Neighborhood
6         M1B  Scarborough                                    Malvern , Rouge
12        M1C  Scarborough           Rouge Hill , Port Union , Highland Creek
18        M1E  Scarborough                Guildwood , Morningside , West Hill
22        M1G  Scarborough                                             Woburn
26        M1H  Scarborough                                          Cedarbrae
..        ...          ...                                                ...
64        M9N         York                                             Weston
70        M9P    Etobicoke                                          Westmount
77        M9R    Etobicoke  Kingsview Village , St. Phillips , Martin Grov...
89        M9V    Etobicoke  South Steeles , Silverstone , Humbergate , Jam...
94        M9W    Etobicoke                                          Northwest

[105 rows x 3 columns]

In [92]:
# coordinates from csv geospatial
df_table.columns
df_2=pd.read_csv('Geospatial_Coordinates.csv')
df_2.rename(columns={'Postal Code': 'PostalCode'},inplace=True)
df_3=pd.merge(df_table[['PostalCode', 'Borough', 'Neighborhood']],df_2, on='PostalCode',how='inner')

In [94]:
#folium map : 
toronto_map= folium.Map(location=[latitude, longitude],tiles='OpenStreetMap', zoom_start=12)
for borough,neighborhood, lat,long in zip(df_3['Borough'],df_3['Neighborhood'],df_3['Latitude'],df_3['Longitude']):
    label=(f'{borough}, {neighborhood}')
    label=folium.Popup(label,parse_html=True)
    folium.CircleMarker(location=[lat,long],
                        popup=label,
                        radius=5, 
                        fill=True,
                        fill_color='#3388ff',
                        fill_opacity=1).add_to(toronto_map)
    
toronto_map